# DATA PROCESSING FOR TRAIN DATA

In [116]:
# Importation des packages

# Base
import importlib
import functions
importlib.reload(functions)
from functions import *


# Data Management
import pandas as pd
import numpy as np

# Modélisation
from sklearn.model_selection import train_test_split
import xgboost as xgb

# Imput
from sklearn.impute import KNNImputer

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


In [117]:
# Importation des données

train_home_team_statistics_df = pd.read_csv('../data/Train_Data/train_home_team_statistics_df.csv', index_col=0)
train_away_team_statistics_df = pd.read_csv('../data/Train_Data/train_away_team_statistics_df.csv', index_col=0)

y_train = pd.read_csv('../data/Y_train_1rknArQ.csv', index_col=0)

In [118]:
# 'LEAGUE' et 'TEAM_NAME' ne sont pas inclus dans les données de soumission.

home_teams = train_home_team_statistics_df.iloc[:,2:]
away_teams = train_away_team_statistics_df.iloc[:,2:]

# Renommer les colonnes pour pouvoir les différencier une fois les deux DF aggrégés.

home_teams.columns = 'HOME_' + home_teams.columns
away_teams.columns = 'AWAY_' + away_teams.columns

# Faire la concaténation
train_data_teams =  pd.concat([home_teams,away_teams],join='inner',axis=1)

# y_train = y_train.loc[train_data.index]
# home_teams.shape --> (12303, 140)
# away_teams.shape --> (12303, 140)

In [119]:
# Traitement des valeurs manquantes pour les statistiques sur les équipes

spot_columns(train_data_teams, percent=0)

Column 'HOME_TEAM_SHOTS_TOTAL_season_sum' has 2.11% NaN values
Column 'HOME_TEAM_SHOTS_INSIDEBOX_season_sum' has 11.26% NaN values
Column 'HOME_TEAM_SHOTS_ON_TARGET_season_sum' has 0.02% NaN values
Column 'HOME_TEAM_SHOTS_OUTSIDEBOX_season_sum' has 11.27% NaN values
Column 'HOME_TEAM_PASSES_season_sum' has 11.49% NaN values
Column 'HOME_TEAM_SUCCESSFUL_PASSES_season_sum' has 11.25% NaN values
Column 'HOME_TEAM_SAVES_season_sum' has 6.34% NaN values
Column 'HOME_TEAM_CORNERS_season_sum' has 0.01% NaN values
Column 'HOME_TEAM_FOULS_season_sum' has 6.15% NaN values
Column 'HOME_TEAM_YELLOWCARDS_season_sum' has 0.04% NaN values
Column 'HOME_TEAM_REDCARDS_season_sum' has 0.28% NaN values
Column 'HOME_TEAM_OFFSIDES_season_sum' has 6.36% NaN values
Column 'HOME_TEAM_PENALTIES_season_sum' has 0.13% NaN values
Column 'HOME_TEAM_SUBSTITUTIONS_season_sum' has 0.37% NaN values
Column 'HOME_TEAM_BALL_SAFE_season_sum' has 2.95% NaN values
Column 'HOME_TEAM_INJURIES_season_sum' has 15.93% NaN values


In [120]:
# nan_colormap(train_data_teams, 'Colormap des valeurs manquantes pour le df d\'entrainement')

# Après observation de la colormap, je pense que les solutions les plus pertinentes pour remplacer
# les valeurs manquantes sont soit de remplacer par des 0 et d'indiquer dans une colonne sous jacente que
# la valeure est originalement manquante, soit de remplacer par la moyenne et de ne rien indiquer. 

# Nouvelle stratégie : Comme on le voit dans la sortie précédente, il y a très peu de NaNs dans chacune 
# des colonnes. Je vais donc remplacer les NaNs par la médiane dans toutes les colonnes où il y a moins de 
# 20% de NaNs et ensuite utiliser une technique de prédiction. 

In [121]:
# # Ma première stratégie va être de remplacer toutes les NaNs par la moyenne de la colonne
# # afin de pouvoir avancer sur la suite.

# # Ne pas oublier les Nones et les Nulls
# train_data_teams = replacing(train_data_teams)

# train_data_teams = nan_imputer(train_data_teams, train_data_teams.columns, 'mean')

In [122]:
# Seconde stratégie

# Je remplis d'abord toutes les colonnes où on observe moins de 20% de NaNs.

for col in train_data_teams.columns[train_data_teams.isna().mean() < 0.51]:
    train_data_teams.fillna({col: train_data_teams[col].median()}, inplace=True)

# spot_columns(train_data_teams, percent=0)

In [123]:
# # Maintenant je remplis le reste avec un KNN Imputer. 

# train_data_teams = train_data_teams.reset_index()

# imputer = KNNImputer(n_neighbors=5)
# train_data_teams = pd.DataFrame(imputer.fit_transform(train_data_teams), columns=train_data_teams.columns)

In [124]:
spot_columns(train_data_teams, percent=0)

In [125]:
# Ajout des données 'joueurs' 

train_home_player_statistics_df = pd.read_csv('../data/Train_Data/train_home_player_statistics_df.csv')
train_away_player_statistics_df = pd.read_csv('../data/Train_Data/train_away_player_statistics_df.csv')

# 'LEAGUE', 'TEAM_NAME' et 'PLAYER_NAME' ne sont pas inclus dans les données de soumission.

home_players = train_home_player_statistics_df.drop(columns=['LEAGUE', 'PLAYER_NAME', 'TEAM_NAME'], axis=1)
away_players = train_away_player_statistics_df.drop(columns=['LEAGUE', 'PLAYER_NAME', 'TEAM_NAME'], axis=1)

# Renommer les colonnes pour pouvoir les différencier une fois les deux DF aggrégés.

home_players.columns = 'HOME_' + home_players.columns
away_players.columns = 'AWAY_' + away_players.columns

home_players = replacing(home_players)
away_players = replacing(away_players)

# home_players.shape --> (237079, 304)
# away_players.shape --> (236132, 304)
# nan_colormap(home_players, 'color map pour les home players')

In [126]:
# Pour le traitement des NaNs dans ces tables, on ajoute le fait
# de supprimer les colonnes où il y a plus de 50% de NaNs. 

spot_columns(home_players, percent=20)

Column 'HOME_PLAYER_CAPTAIN_season_sum' has 89.33% NaN values
Column 'HOME_PLAYER_DRIBBLED_ATTEMPTS_season_sum' has 22.82% NaN values
Column 'HOME_PLAYER_DRIBBLED_PAST_season_sum' has 22.82% NaN values
Column 'HOME_PLAYER_SUCCESSFUL_DRIBBLES_season_sum' has 22.82% NaN values
Column 'HOME_PLAYER_PUNCHES_season_sum' has 71.54% NaN values
Column 'HOME_PLAYER_LONG_BALLS_season_sum' has 100.00% NaN values
Column 'HOME_PLAYER_LONG_BALLS_WON_season_sum' has 100.00% NaN values
Column 'HOME_PLAYER_SHOTS_OFF_TARGET_season_sum' has 100.00% NaN values
Column 'HOME_PLAYER_ACCURATE_PASSES_PERCENTAGE_season_average' has 29.75% NaN values
Column 'HOME_PLAYER_CAPTAIN_season_average' has 100.00% NaN values
Column 'HOME_PLAYER_DRIBBLED_ATTEMPTS_season_average' has 22.82% NaN values
Column 'HOME_PLAYER_DRIBBLED_PAST_season_average' has 22.82% NaN values
Column 'HOME_PLAYER_SUCCESSFUL_DRIBBLES_season_average' has 22.82% NaN values
Column 'HOME_PLAYER_PUNCHES_season_average' has 71.54% NaN values
Column 'HO

In [127]:
spot_columns(away_players, percent=20)

Column 'AWAY_PLAYER_CAPTAIN_season_sum' has 89.42% NaN values
Column 'AWAY_PLAYER_DRIBBLED_ATTEMPTS_season_sum' has 22.94% NaN values
Column 'AWAY_PLAYER_DRIBBLED_PAST_season_sum' has 22.94% NaN values
Column 'AWAY_PLAYER_SUCCESSFUL_DRIBBLES_season_sum' has 22.94% NaN values
Column 'AWAY_PLAYER_PUNCHES_season_sum' has 71.60% NaN values
Column 'AWAY_PLAYER_LONG_BALLS_season_sum' has 100.00% NaN values
Column 'AWAY_PLAYER_LONG_BALLS_WON_season_sum' has 100.00% NaN values
Column 'AWAY_PLAYER_SHOTS_OFF_TARGET_season_sum' has 100.00% NaN values
Column 'AWAY_PLAYER_ACCURATE_PASSES_PERCENTAGE_season_average' has 29.97% NaN values
Column 'AWAY_PLAYER_CAPTAIN_season_average' has 100.00% NaN values
Column 'AWAY_PLAYER_DRIBBLED_ATTEMPTS_season_average' has 22.94% NaN values
Column 'AWAY_PLAYER_DRIBBLED_PAST_season_average' has 22.94% NaN values
Column 'AWAY_PLAYER_SUCCESSFUL_DRIBBLES_season_average' has 22.94% NaN values
Column 'AWAY_PLAYER_PUNCHES_season_average' has 71.60% NaN values
Column 'AW

In [128]:
# Suppression des colonnes avec plus de 50% de NaNs. 

home_players = home_players.drop(columns=home_players.columns[home_players.isna().mean() > 0.5])
away_players = away_players.drop(columns=away_players.columns[away_players.isna().mean() > 0.5])

In [129]:
home_players.to_csv('../data/Train_Data/home_players_df.csv')
away_players.to_csv('../data/Train_Data/away_players_df.csv')

In [130]:
spot_columns(home_players, percent=20)

Column 'HOME_PLAYER_DRIBBLED_ATTEMPTS_season_sum' has 22.82% NaN values
Column 'HOME_PLAYER_DRIBBLED_PAST_season_sum' has 22.82% NaN values
Column 'HOME_PLAYER_SUCCESSFUL_DRIBBLES_season_sum' has 22.82% NaN values
Column 'HOME_PLAYER_ACCURATE_PASSES_PERCENTAGE_season_average' has 29.75% NaN values
Column 'HOME_PLAYER_DRIBBLED_ATTEMPTS_season_average' has 22.82% NaN values
Column 'HOME_PLAYER_DRIBBLED_PAST_season_average' has 22.82% NaN values
Column 'HOME_PLAYER_SUCCESSFUL_DRIBBLES_season_average' has 22.82% NaN values
Column 'HOME_PLAYER_ACCURATE_PASSES_PERCENTAGE_season_std' has 34.54% NaN values
Column 'HOME_PLAYER_DRIBBLED_ATTEMPTS_season_std' has 24.01% NaN values
Column 'HOME_PLAYER_DRIBBLED_PAST_season_std' has 24.01% NaN values
Column 'HOME_PLAYER_SUCCESSFUL_DRIBBLES_season_std' has 24.01% NaN values
Column 'HOME_PLAYER_DRIBBLED_ATTEMPTS_5_last_match_sum' has 22.82% NaN values
Column 'HOME_PLAYER_DRIBBLED_PAST_5_last_match_sum' has 22.82% NaN values
Column 'HOME_PLAYER_PENALTIE

In [131]:
spot_columns(away_players, percent=20)

Column 'AWAY_PLAYER_DRIBBLED_ATTEMPTS_season_sum' has 22.94% NaN values
Column 'AWAY_PLAYER_DRIBBLED_PAST_season_sum' has 22.94% NaN values
Column 'AWAY_PLAYER_SUCCESSFUL_DRIBBLES_season_sum' has 22.94% NaN values
Column 'AWAY_PLAYER_ACCURATE_PASSES_PERCENTAGE_season_average' has 29.97% NaN values
Column 'AWAY_PLAYER_DRIBBLED_ATTEMPTS_season_average' has 22.94% NaN values
Column 'AWAY_PLAYER_DRIBBLED_PAST_season_average' has 22.94% NaN values
Column 'AWAY_PLAYER_SUCCESSFUL_DRIBBLES_season_average' has 22.94% NaN values
Column 'AWAY_PLAYER_ACCURATE_PASSES_PERCENTAGE_season_std' has 34.77% NaN values
Column 'AWAY_PLAYER_DRIBBLED_ATTEMPTS_season_std' has 24.17% NaN values
Column 'AWAY_PLAYER_DRIBBLED_PAST_season_std' has 24.17% NaN values
Column 'AWAY_PLAYER_SUCCESSFUL_DRIBBLES_season_std' has 24.17% NaN values
Column 'AWAY_PLAYER_DRIBBLED_ATTEMPTS_5_last_match_sum' has 22.94% NaN values
Column 'AWAY_PLAYER_DRIBBLED_PAST_5_last_match_sum' has 22.94% NaN values
Column 'AWAY_PLAYER_PENALTIE

In [132]:
# Je remplis ensuite toutes les colonnes où on observe moins de 20% de NaNs.

home_players = home_players.fillna({'HOME_POSITION': home_players['HOME_POSITION'].mode()[0]})

for col in home_players.columns[home_players.isna().mean() < 0.51]:
    if home_players[col].dtype in ['float64', 'int64']:
        home_players.fillna({col: home_players[col].median()}, inplace=True)


spot_columns(home_players, percent=0)
# Il ne reste que celles comprises entre 20% et 50%

In [133]:
# Je remplis ensuite toutes les colonnes où on observe moins de 20% de NaNs.

away_players = away_players.fillna({'AWAY_POSITION': away_players['AWAY_POSITION'].mode()[0]})

for col in away_players.columns[away_players.isna().mean() < 0.51]:
    if away_players[col].dtype in ['float64', 'int64']:
        away_players.fillna({col: away_players[col].median()}, inplace=True)

spot_columns(away_players, percent=0)
# Il ne reste que celles comprises entre 20% et 50%

In [134]:
# Maintenant je remplis le reste avec un KNN Imputer. 

# imputer_home = KNNImputer(n_neighbors=3)
# home_players_imputed = pd.DataFrame(
#     imputer_home.fit_transform(home_players.drop(columns=['HOME_POSITION'], axis=1)),
#     columns=home_players.columns.drop('HOME_POSITION')
# )

# home_players = pd.concat([home_players['HOME_POSITION'], home_players_imputed], axis=1)

# home_players.head(5)

In [135]:
# imputer_away = KNNImputer(n_neighbors=3)
# away_players_imputed = pd.DataFrame(
#     imputer_away.fit_transform(away_players.drop(columns=['AWAY_POSITION'], axis=1)),
#     columns=away_players.columns.drop('AWAY_POSITION')
# )

# away_players = pd.concat([away_players['AWAY_POSITION'], away_players_imputed], axis=1)

# away_players.head(5)

In [136]:
# Je remets les colonnes dans le bonne ordre même si ce n'est pas obligatoire.

# cols = list(home_players.columns)
# col1_idx, col2_idx = cols.index('HOME_POSITION'), cols.index('HOME_ID')
# cols[col1_idx], cols[col2_idx] = cols[col2_idx], cols[col1_idx]
# home_players = home_players[cols]

# cols = list(away_players.columns)
# col1_idx, col2_idx = cols.index('AWAY_POSITION'), cols.index('AWAY_ID')
# cols[col1_idx], cols[col2_idx] = cols[col2_idx], cols[col1_idx]
# away_players = away_players[cols]

In [137]:
# Je vais agréger les colonnes par poste et par matchs pour réduire la taile du dataframe des joueurs.
# Il est important de le faire avant la fusion pour garder un lien entre les joueurs et les équipes comme 
# TEAM_NAME n'est pas dans le dataframe de soumission. 

columns_to_aggregate_home = [col for col in home_players.columns if col.endswith(('sum', 'std'))]
columns_to_aggregate_away = [col for col in away_players.columns if col.endswith(('sum', 'std'))]

# len(columns_to_aggregate_home)
# On garde 98+2 colonnes.

In [138]:
# Création des tables home_agg et away_agg pour les agréger avec la table train_data_teams.

home_agg = home_players.groupby(['HOME_ID', 'HOME_POSITION']).agg({
    col: ['mean', 'max', 'min', 'median'] for col in columns_to_aggregate_home  # Agréger par la moyenne
}).reset_index()

away_agg = away_players.groupby(['AWAY_ID', 'AWAY_POSITION']).agg({
    col: ['mean', 'max', 'min', 'median'] for col in columns_to_aggregate_away  # Agréger par la moyenne également
}).reset_index()

home_agg.head(5)
# away_agg.head(5)

HOME_ID HOME_POSITION HOME_PLAYER_ACCURATE_CROSSES_season_sum              \
                                                           mean    max  min   
0       0      defender                                     4.0   14.0  0.0   
1       0    goalkeeper                                     0.0    0.0  0.0   
2       0    midfielder                                    16.0  100.0  0.0   
3       1      defender                                     5.6   25.0  0.0   
4       1    goalkeeper                                     0.0    0.0  0.0   

         HOME_PLAYER_ACCURATE_PASSES_season_sum                    \
  median                                   mean   max  min median   
0    1.0                              27.166667  52.0  7.0   28.0   
1    0.0                              16.500000  33.0  0.0   16.5   
2    3.5                              18.800000  44.0  5.0   19.0   
3    0.0                              57.200000  92.0  7.0   65.0   
4    0.0                              14.000000  28.0  0.0   14.0   

  HOME_PLAYER_AERIALS_WON_season_sum                     \
                                mean   max   min median   
0                          22.166667  52.0   4.0   13.0   
1                           1.000000   2.0   0.0    1.0   
2                          14.000000  38.0   2.0   10.0   
3                          32.400000  56.0  10.0   34.0   
4                           3.000000   6.0   0.0    3.0   

  HOME_PLAYER_ASSISTS_season_sum                    \
                            mean   max  min median   
0                            7.0  28.0  0.0    0.0   
1                            0.0   0.0  0.0    0.0   
2                            9.8  28.0  0.0   14.0   
3                            8.0  20.0  0.0    0.0   
4                            0.0   0.0  0.0    0.0   

  HOME_PLAYER_BIG_CHANCES_CREATED_season_sum                    \
                                        mean   max  min median   
0                                   5.333333  16.0  0.0    4.0   
1                                   0.000000   0.0  0.0    0.0   
2                                   9.800000  33.0  0.0    8.0   
3                                   2.400000  12.0  0.0    0.0   
4                                   0.000000   0.0  0.0    0.0   

  HOME_PLAYER_BIG_CHANCES_MISSED_season_sum                    \
                                       mean   max  min median   
0                                       0.0   0.0  0.0    0.0   
1                                       0.0   0.0  0.0    0.0   
2                                      11.1  37.0  0.0    0.0   
3                                       3.2  16.0  0.0    0.0   
4                                       0.0   0.0  0.0    0.0   

  HOME_PLAYER_BLOCKED_SHOTS_season_sum                    \
                                  mean   max  min median   
0                                 17.5  62.0  0.0    9.0   
1                                  0.0   0.0  0.0    0.0   
2                                  6.1  31.0  0.0    3.0   
3                                 26.4  41.0  0.0   25.0   
4                                  0.0   0.0  0.0    0.0   

  HOME_PLAYER_CLEARANCES_season_sum                      \
                               mean    max   min median   
0                         34.833333   59.0   4.0   37.5   
1                          8.000000   16.0   0.0    8.0   
2                          7.600000   25.0   0.0    4.5   
3                         48.000000  100.0  16.0   41.0   
4                          3.500000    7.0   0.0    3.5   

  HOME_PLAYER_CLEARANCE_OFFLINE_season_sum                    \
                                      mean   max  min median   
0                                 8.333333  50.0  0.0    0.0   
1                                 0.000000   0.0  0.0    0.0   
2                                 0.000000   0.0  0.0    0.0   
3                                10.000000  50.0  0.0    0.0   
4                                

In [139]:
# Aplatir les colonnes multi-niveaux générées par le groupby ou agrégations précédentes
home_agg.columns = ['_'.join(col).strip() for col in home_agg.columns.values]
home_agg = home_agg.rename(columns={'HOME_ID_' : 'HOME_ID', 'HOME_POSITION_' : 'HOME_POSITION'})

home_agg.head(5)

HOME_ID HOME_POSITION  HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean  \
0        0      defender                                           4.0   
1        0    goalkeeper                                           0.0   
2        0    midfielder                                          16.0   
3        1      defender                                           5.6   
4        1    goalkeeper                                           0.0   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_max  \
0                                         14.0   
1                                          0.0   
2                                        100.0   
3                                         25.0   
4                                          0.0   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min  \
0                                          0.0   
1                                          0.0   
2                                          0.0   
3                                          0.0   
4                                          0.0   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_median  \
0                                             1.0   
1                                             0.0   
2                                             3.5   
3                                             0.0   
4                                             0.0   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_mean  \
0                                    27.166667   
1                                    16.500000   
2                                    18.800000   
3                                    57.200000   
4                                    14.000000   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_max  \
0                                        52.0   
1                                        33.0   
2                                        44.0   
3                                        92.0   
4                                        28.0   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_min  \
0                                         7.0   
1                                         0.0   
2                                         5.0   
3                                         7.0   
4                                         0.0   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_median  \
0                                           28.0   
1                                           16.5   
2                                           19.0   
3                                           65.0   
4                                           14.0   

   HOME_PLAYER_AERIALS_WON_season_sum_mean  \
0                                22.166667   
1                                 1.000000   
2                                14.000000   
3                                32.400000   
4                                 3.000000   

   HOME_PLAYER_AERIALS_WON_season_sum_max  \
0                                    52.0   
1                                     2.0   
2                                    38.0   
3                                    56.0   
4                                     6.0   

   HOME_PLAYER_AERIALS_WON_season_sum_min  \
0                                     4.0   
1                                     0.0   
2                                     2.0   
3                                    10.0   
4                                     0.0   

   HOME_PLAYER_AERIALS_WON_season_sum_median  \
0                                       13.0   
1                                        1.0   
2                                       10.0   
3                                       34.0   
4                                        3.0   

   HOME_PLAYER_ASSISTS_season_sum_mean  HOME_PLAYER_ASSISTS_season_sum_max  \
0                                  7.0                                28.0   
1                                  0.0                                 0.0   
2                                  9.8                                28.0   
3            

In [100]:
# Aplatir les colonnes multi-niveaux générées par le groupby ou agrégations précédentes
away_agg.columns = ['_'.join(col).strip() for col in away_agg.columns.values]
away_agg = away_agg.rename(columns={'AWAY_ID_' : 'AWAY_ID', 'AWAY_POSITION_' : 'AWAY_POSITION'})

away_agg.head(5)

AWAY_ID AWAY_POSITION  AWAY_PLAYER_ACCURATE_CROSSES_season_sum_mean  \
0        0      defender                                      6.600000   
1        0    goalkeeper                                      0.000000   
2        0    midfielder                                      8.727273   
3        1      defender                                      1.714286   
4        1    goalkeeper                                      0.000000   

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_max  \
0                                         25.0   
1                                          0.0   
2                                         51.0   
3                                          9.0   
4                                          0.0   

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_min  \
0                                          0.0   
1                                          0.0   
2                                          0.0   
3                                          0.0   
4                                          0.0   

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_median  \
0                                             0.0   
1                                             0.0   
2                                             5.0   
3                                             0.0   
4                                             0.0   

   AWAY_PLAYER_ACCURATE_PASSES_season_sum_mean  \
0                                    33.400000   
1                                    13.500000   
2                                    25.909091   
3                                    31.142857   
4                                    15.500000   

   AWAY_PLAYER_ACCURATE_PASSES_season_sum_max  \
0                                        50.0   
1                                        27.0   
2                                        64.0   
3                                        48.0   
4                                        16.0   

   AWAY_PLAYER_ACCURATE_PASSES_season_sum_min  \
0                                         0.0   
1                                         0.0   
2                                         1.0   
3                                        12.0   
4                                        15.0   

   AWAY_PLAYER_ACCURATE_PASSES_season_sum_median  \
0                                           48.0   
1                                           13.5   
2                                           19.0   
3                                           33.0   
4                                           15.5   

   AWAY_PLAYER_AERIALS_WON_season_sum_mean  \
0                                23.600000   
1                                 2.500000   
2                                11.000000   
3                                20.285714   
4                                 0.500000   

   AWAY_PLAYER_AERIALS_WON_season_sum_max  \
0                                    36.0   
1                                     5.0   
2                                    31.0   
3                                    46.0   
4                                     1.0   

   AWAY_PLAYER_AERIALS_WON_season_sum_min  \
0                                     0.0   
1                                     0.0   
2                                     0.0   
3                                     8.0   
4                                     0.0   

   AWAY_PLAYER_AERIALS_WON_season_sum_median  \
0                                       30.0   
1                                        2.5   
2                                        6.0   
3                                       10.0   
4                                        0.5   

   AWAY_PLAYER_ASSISTS_season_sum_mean  AWAY_PLAYER_ASSISTS_season_sum_max  \
0                             5.600000                                14.0   
1                             0.000000                                 0.0   
2                            10.181818                                42.0   
3            

In [141]:
home_agg.columns

Index(['HOME_ID', 'HOME_POSITION',
       'HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean',
       'HOME_PLAYER_ACCURATE_CROSSES_season_sum_max',
       'HOME_PLAYER_ACCURATE_CROSSES_season_sum_min',
       'HOME_PLAYER_ACCURATE_CROSSES_season_sum_median',
       'HOME_PLAYER_ACCURATE_PASSES_season_sum_mean',
       'HOME_PLAYER_ACCURATE_PASSES_season_sum_max',
       'HOME_PLAYER_ACCURATE_PASSES_season_sum_min',
       'HOME_PLAYER_ACCURATE_PASSES_season_sum_median',
       ...
       'HOME_PLAYER_TOTAL_CROSSES_5_last_match_std_min',
       'HOME_PLAYER_TOTAL_CROSSES_5_last_match_std_median',
       'HOME_PLAYER_TOTAL_DUELS_5_last_match_std_mean',
       'HOME_PLAYER_TOTAL_DUELS_5_last_match_std_max',
       'HOME_PLAYER_TOTAL_DUELS_5_last_match_std_min',
       'HOME_PLAYER_TOTAL_DUELS_5_last_match_std_median',
       'HOME_PLAYER_YELLOWCARDS_5_last_match_std_mean',
       'HOME_PLAYER_YELLOWCARDS_5_last_match_std_max',
       'HOME_PLAYER_YELLOWCARDS_5_last_match_std_min',
       'HOM

In [140]:
# Pivot pour home_agg
home_pivot = home_agg.pivot(index='HOME_ID', columns='HOME_POSITION', values=columns_to_aggregate_home)

home_pivot.head(5)

KeyError: "None of [Index(['HOME_PLAYER_ACCURATE_CROSSES_season_sum',\n       'HOME_PLAYER_ACCURATE_PASSES_season_sum',\n       'HOME_PLAYER_AERIALS_WON_season_sum', 'HOME_PLAYER_ASSISTS_season_sum',\n       'HOME_PLAYER_BIG_CHANCES_CREATED_season_sum',\n       'HOME_PLAYER_BIG_CHANCES_MISSED_season_sum',\n       'HOME_PLAYER_BLOCKED_SHOTS_season_sum',\n       'HOME_PLAYER_CLEARANCES_season_sum',\n       'HOME_PLAYER_CLEARANCE_OFFLINE_season_sum',\n       'HOME_PLAYER_DISPOSSESSED_season_sum',\n       ...\n       'HOME_PLAYER_SAVES_INSIDE_BOX_5_last_match_std',\n       'HOME_PLAYER_SHOTS_BLOCKED_5_last_match_std',\n       'HOME_PLAYER_SHOTS_ON_TARGET_5_last_match_std',\n       'HOME_PLAYER_SHOTS_TOTAL_5_last_match_std',\n       'HOME_PLAYER_STARTING_LINEUP_5_last_match_std',\n       'HOME_PLAYER_SUCCESSFUL_DRIBBLES_5_last_match_std',\n       'HOME_PLAYER_TACKLES_5_last_match_std',\n       'HOME_PLAYER_TOTAL_CROSSES_5_last_match_std',\n       'HOME_PLAYER_TOTAL_DUELS_5_last_match_std',\

In [25]:
# Aplatir les colonnes multi-niveaux générées par pivot_table
home_pivot.columns = ['_'.join(col).strip() for col in home_pivot.columns.values]
home_pivot.reset_index(inplace=True)

home_pivot.head(5)

# Tout fonctionne bien, il ne restera plus qu'à traiter les NaNs. 

HOME_ID  HOME_PLAYER_ACCURATE_CROSSES_season_sum_attacker  \
0        0                                               NaN   
1        1                                               NaN   
2        2                                              5.00   
3        3                                              2.50   
4        4                                             18.75   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_defender  \
0                                          4.000000   
1                                          5.600000   
2                                          8.857143   
3                                          0.500000   
4                                          0.200000   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_goalkeeper  \
0                                                0.0    
1                                                0.0    
2                                                0.0    
3                                                0.0    
4                                                0.0    

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_midfielder  \
0                                          16.000000    
1                                          12.545455    
2                                          11.200000    
3                                          18.500000    
4                                          14.142857    

   HOME_PLAYER_ACCURATE_PASSES_season_sum_attacker  \
0                                              NaN   
1                                              NaN   
2                                             5.25   
3                                            13.25   
4                                            20.25   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_defender  \
0                                        27.166667   
1                                        57.200000   
2                                        22.714286   
3                                        52.750000   
4                                        24.600000   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_goalkeeper  \
0                                               16.5   
1                                               14.0   
2                                               11.5   
3                                               20.5   
4                                                8.5   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_midfielder  \
0                                          18.800000   
1                                          23.090909   
2                                          17.900000   
3                                          38.500000   
4                                          35.000000   

   HOME_PLAYER_AERIALS_WON_season_sum_attacker  \
0                                          NaN   
1                                          NaN   
2                                         6.75   
3                                        13.25   
4                                        14.50   

   HOME_PLAYER_AERIALS_WON_season_sum_defender  \
0                                    22.166667   
1                                    32.400000   
2                                    20.571429   
3                                    36.250000   
4                                    16.600000   

   HOME_PLAYER_AERIALS_WON_season_sum_goalkeeper  \
0                                            1.0   
1                                            3.0   
2                                            2.0   
3                                            2.0   
4                                            1.5   

   HOME_PLAYER_AERIALS_WON_season_sum_midfielder  \
0                                      14.000000   
1                                       8.545455   
2                                      17.800000   
3                                      10.375000   
4                                      18.285714   

   HOME_PLAYER_ASSISTS_season_sum_attacker  \
0  

In [75]:
# Pivot pour away_agg
away_pivot = away_agg.pivot(index='AWAY_ID', columns='AWAY_POSITION', values=columns_to_aggregate_away)

# Aplatir les colonnes multi-niveaux générées par pivot_table
away_pivot.columns = ['_'.join(col).strip() for col in away_pivot.columns.values]
away_pivot.reset_index(inplace=True)

away_pivot.head(5)

KeyError: "None of [Index(['AWAY_PLAYER_ACCURATE_CROSSES_season_sum',\n       'AWAY_PLAYER_ACCURATE_PASSES_season_sum',\n       'AWAY_PLAYER_AERIALS_WON_season_sum', 'AWAY_PLAYER_ASSISTS_season_sum',\n       'AWAY_PLAYER_BIG_CHANCES_CREATED_season_sum',\n       'AWAY_PLAYER_BIG_CHANCES_MISSED_season_sum',\n       'AWAY_PLAYER_BLOCKED_SHOTS_season_sum',\n       'AWAY_PLAYER_CLEARANCES_season_sum',\n       'AWAY_PLAYER_CLEARANCE_OFFLINE_season_sum',\n       'AWAY_PLAYER_DISPOSSESSED_season_sum',\n       ...\n       'AWAY_PLAYER_SAVES_INSIDE_BOX_5_last_match_std',\n       'AWAY_PLAYER_SHOTS_BLOCKED_5_last_match_std',\n       'AWAY_PLAYER_SHOTS_ON_TARGET_5_last_match_std',\n       'AWAY_PLAYER_SHOTS_TOTAL_5_last_match_std',\n       'AWAY_PLAYER_STARTING_LINEUP_5_last_match_std',\n       'AWAY_PLAYER_SUCCESSFUL_DRIBBLES_5_last_match_std',\n       'AWAY_PLAYER_TACKLES_5_last_match_std',\n       'AWAY_PLAYER_TOTAL_CROSSES_5_last_match_std',\n       'AWAY_PLAYER_TOTAL_DUELS_5_last_match_std',\

In [27]:
# Je fais maintenant le merge sur l'ID des matchs. 

home_pivot.rename(columns={'HOME_ID': 'ID'}, inplace=True)
away_pivot.rename(columns={'AWAY_ID': 'ID'}, inplace=True)

train_data_players = home_pivot.merge(away_pivot, on='ID', how='inner')

train_data_players.head(5)

ID  HOME_PLAYER_ACCURATE_CROSSES_season_sum_attacker  \
0   0                                               NaN   
1   1                                               NaN   
2   2                                              5.00   
3   3                                              2.50   
4   4                                             18.75   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_defender  \
0                                          4.000000   
1                                          5.600000   
2                                          8.857143   
3                                          0.500000   
4                                          0.200000   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_goalkeeper  \
0                                                0.0    
1                                                0.0    
2                                                0.0    
3                                                0.0    
4                                                0.0    

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_midfielder  \
0                                          16.000000    
1                                          12.545455    
2                                          11.200000    
3                                          18.500000    
4                                          14.142857    

   HOME_PLAYER_ACCURATE_PASSES_season_sum_attacker  \
0                                              NaN   
1                                              NaN   
2                                             5.25   
3                                            13.25   
4                                            20.25   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_defender  \
0                                        27.166667   
1                                        57.200000   
2                                        22.714286   
3                                        52.750000   
4                                        24.600000   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_goalkeeper  \
0                                               16.5   
1                                               14.0   
2                                               11.5   
3                                               20.5   
4                                                8.5   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_midfielder  \
0                                          18.800000   
1                                          23.090909   
2                                          17.900000   
3                                          38.500000   
4                                          35.000000   

   HOME_PLAYER_AERIALS_WON_season_sum_attacker  \
0                                          NaN   
1                                          NaN   
2                                         6.75   
3                                        13.25   
4                                        14.50   

   HOME_PLAYER_AERIALS_WON_season_sum_defender  \
0                                    22.166667   
1                                    32.400000   
2                                    20.571429   
3                                    36.250000   
4                                    16.600000   

   HOME_PLAYER_AERIALS_WON_season_sum_goalkeeper  \
0                                            1.0   
1                                            3.0   
2                                            2.0   
3                                            2.0   
4                                            1.5   

   HOME_PLAYER_AERIALS_WON_season_sum_midfielder  \
0                                      14.000000   
1                                       8.545455   
2                                      17.800000   
3                                      10.375000   
4                                      18.285714   

   HOME_PLAYER_ASSISTS_season_sum_attacker  \
0                                

In [28]:
spot_columns(train_data_players, 50)

Column 'HOME_PLAYER_ACCURATE_CROSSES_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_ACCURATE_PASSES_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_AERIALS_WON_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_ASSISTS_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_BIG_CHANCES_MISSED_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_BLOCKED_SHOTS_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_CLEARANCES_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_CLEARANCE_OFFLINE_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_DISPOSSESSED_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_DRIBBLED_ATTEMPTS_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_DRIBBLED_PAST_season_sum_attacker' has 53.00% NaN values
Column 'HOME_PLAYER_DUELS_LOST_season_sum_attacker' has 53.00% N

In [29]:
# À nouveau, je supprime toutes les colonnes où il y a plus de 50% de NaNs.

train_data_players = train_data_players.drop(columns=train_data_players.columns[train_data_players.isna().mean() > 0.5])

In [30]:
train_data_players.to_csv('../data/Train_Data/players_df.csv')

In [31]:
spot_columns(train_data_players, percent=0)

Column 'HOME_PLAYER_ACCURATE_CROSSES_season_sum_defender' has 9.00% NaN values
Column 'HOME_PLAYER_ACCURATE_CROSSES_season_sum_goalkeeper' has 6.96% NaN values
Column 'HOME_PLAYER_ACCURATE_PASSES_season_sum_defender' has 9.00% NaN values
Column 'HOME_PLAYER_ACCURATE_PASSES_season_sum_goalkeeper' has 6.96% NaN values
Column 'HOME_PLAYER_AERIALS_WON_season_sum_defender' has 9.00% NaN values
Column 'HOME_PLAYER_AERIALS_WON_season_sum_goalkeeper' has 6.96% NaN values
Column 'HOME_PLAYER_ASSISTS_season_sum_defender' has 9.00% NaN values
Column 'HOME_PLAYER_ASSISTS_season_sum_goalkeeper' has 6.96% NaN values
Column 'HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_defender' has 9.00% NaN values
Column 'HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_goalkeeper' has 6.96% NaN values
Column 'HOME_PLAYER_BIG_CHANCES_MISSED_season_sum_defender' has 9.00% NaN values
Column 'HOME_PLAYER_BIG_CHANCES_MISSED_season_sum_goalkeeper' has 6.96% NaN values
Column 'HOME_PLAYER_BLOCKED_SHOTS_season_sum_defender' has 9

In [32]:
# Il reste des colonnes dans lesquelles il y a moins de 10% de NaNs.
# Je vais donc remplacer ces NaNs par les médianes des colonnes concernées.

for col in train_data_players.columns[train_data_players.isna().mean() < 1]:
    train_data_players.fillna({col: train_data_players[col].median()}, inplace=True)

In [33]:
spot_columns(train_data_players, percent=0)

In [34]:
train_data_players.head(5)

ID  HOME_PLAYER_ACCURATE_CROSSES_season_sum_defender  \
0   0                                          4.000000   
1   1                                          5.600000   
2   2                                          8.857143   
3   3                                          0.500000   
4   4                                          0.200000   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_goalkeeper  \
0                                                0.0    
1                                                0.0    
2                                                0.0    
3                                                0.0    
4                                                0.0    

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_midfielder  \
0                                          16.000000    
1                                          12.545455    
2                                          11.200000    
3                                          18.500000    
4                                          14.142857    

   HOME_PLAYER_ACCURATE_PASSES_season_sum_defender  \
0                                        27.166667   
1                                        57.200000   
2                                        22.714286   
3                                        52.750000   
4                                        24.600000   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_goalkeeper  \
0                                               16.5   
1                                               14.0   
2                                               11.5   
3                                               20.5   
4                                                8.5   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_midfielder  \
0                                          18.800000   
1                                          23.090909   
2                                          17.900000   
3                                          38.500000   
4                                          35.000000   

   HOME_PLAYER_AERIALS_WON_season_sum_defender  \
0                                    22.166667   
1                                    32.400000   
2                                    20.571429   
3                                    36.250000   
4                                    16.600000   

   HOME_PLAYER_AERIALS_WON_season_sum_goalkeeper  \
0                                            1.0   
1                                            3.0   
2                                            2.0   
3                                            2.0   
4                                            1.5   

   HOME_PLAYER_AERIALS_WON_season_sum_midfielder  \
0                                      14.000000   
1                                       8.545455   
2                                      17.800000   
3                                      10.375000   
4                                      18.285714   

   HOME_PLAYER_ASSISTS_season_sum_defender  \
0                                      7.0   
1                                      8.0   
2                                      1.0   
3                                      4.5   
4                                      1.2   

   HOME_PLAYER_ASSISTS_season_sum_goalkeeper  \
0                                        0.0   
1                                        0.0   
2                                        0.0   
3                                        0.0   
4                                        0.0   

   HOME_PLAYER_ASSISTS_season_sum_midfielder  \
0                                   9.800000   
1                                  23.636364   
2                                   5.100000   
3                                  19.125000   
4                                   7.000000   

   HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_defender  \
0                                           5.333333     
1                                           2.400000     
2      

In [35]:
# Je finis avec les colonnes comprises entre 10% et 50%.

# imputer_final = KNNImputer(n_neighbors=5)
# train_data_players = pd.DataFrame(
#     imputer_final.fit_transform(train_data_players),
#     columns=train_data_players.columns
# )

# spot_columns(train_data_players, percent=0)

In [36]:
train_data_players.shape

(12303, 1081)

In [37]:
train_data_players.head(1)

ID  HOME_PLAYER_ACCURATE_CROSSES_season_sum_defender  \
0   0                                               4.0   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_goalkeeper  \
0                                                0.0    

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_midfielder  \
0                                               16.0    

   HOME_PLAYER_ACCURATE_PASSES_season_sum_defender  \
0                                        27.166667   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_goalkeeper  \
0                                               16.5   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_midfielder  \
0                                               18.8   

   HOME_PLAYER_AERIALS_WON_season_sum_defender  \
0                                    22.166667   

   HOME_PLAYER_AERIALS_WON_season_sum_goalkeeper  \
0                                            1.0   

   HOME_PLAYER_AERIALS_WON_season_sum_midfielder  \
0                                           14.0   

   HOME_PLAYER_ASSISTS_season_sum_defender  \
0                                      7.0   

   HOME_PLAYER_ASSISTS_season_sum_goalkeeper  \
0                                        0.0   

   HOME_PLAYER_ASSISTS_season_sum_midfielder  \
0                                        9.8   

   HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_defender  \
0                                           5.333333     

   HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_goalkeeper  \
0                                                0.0       

   HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_midfielder  \
0                                                9.8       

   HOME_PLAYER_BIG_CHANCES_MISSED_season_sum_defender  \
0                                                0.0    

   HOME_PLAYER_BIG_CHANCES_MISSED_season_sum_goalkeeper  \
0                                                0.0      

   HOME_PLAYER_BIG_CHANCES_MISSED_season_sum_midfielder  \
0                                               11.1      

   HOME_PLAYER_BLOCKED_SHOTS_season_sum_defender  \
0                                           17.5   

   HOME_PLAYER_BLOCKED_SHOTS_season_sum_goalkeeper  \
0                                              0.0   

   HOME_PLAYER_BLOCKED_SHOTS_season_sum_midfielder  \
0                                              6.1   

   HOME_PLAYER_CLEARANCES_season_sum_defender  \
0                                   34.833333   

   HOME_PLAYER_CLEARANCES_season_sum_goalkeeper  \
0                                           8.0   

   HOME_PLAYER_CLEARANCES_season_sum_midfielder  \
0                                           7.6   

   HOME_PLAYER_CLEARANCE_OFFLINE_season_sum_defender  \
0                                           8.333333   

   HOME_PLAYER_CLEARANCE_OFFLINE_season_sum_goalkeeper  \
0                                                0.0     

   HOME_PLAYER_CLEARANCE_OFFLINE_season_sum_midfielder  \
0                                                0.0     

   HOME_PLAYER_DISPOSSESSED_season_sum_defender  \
0                                          10.0   

   HOME_PLAYER_DISPOSSESSED_season_sum_goalkeeper  \
0                                             0.0   

   HOME_PLAYER_DISPOSSESSED_season_sum_midfielder  \
0                                            25.7   

   HOME_PLAYER_DRIBBLED_ATTEMPTS_season_sum_defender  \
0                                           6.333333   

   HOME_PLAYER_DRIBBLED_ATTEMPTS_season_sum_goalkeeper  \
0                                                0.0     

   HOME_PLAYER_DRIBBLED_ATTEMPTS_season_sum_midfielder  \
0                                               17.3     

   HOME_PLAYER_DRIBBLED_PAST_season_sum_defender  \
0                                           22.0   

   HOME_PLAYER_DRIBBLED_PAST_season_sum_goalkeeper  \
0                                              0.0   

   HOME_PLAYER_DRIBBLED_PAST_season_sum_midfielder  \
0                                             17.3   

   HOME_PLAYER_DUELS_LOST_season_sum_defender  

In [38]:
# Fusionner avec les données des équipes.
train_data = train_data_teams.merge(train_data_players, on='ID', how='left')

train_data = train_data.set_index('ID')

train_data.head(5)

HOME_TEAM_SHOTS_TOTAL_season_sum  HOME_TEAM_SHOTS_INSIDEBOX_season_sum  \
ID                                                                           
0                                3.0                                   2.0   
1                                6.0                                   8.0   
2                                4.0                                   2.0   
3                                7.0                                   5.0   
4                                3.0                                   3.0   

    HOME_TEAM_SHOTS_OFF_TARGET_season_sum  \
ID                                          
0                                     5.0   
1                                     3.0   
2                                     5.0   
3                                     5.0   
4                                     2.0   

    HOME_TEAM_SHOTS_ON_TARGET_season_sum  \
ID                                         
0                                    2.0   
1                                    6.0   
2                                    2.0   
3                                    6.0   
4                                    3.0   

    HOME_TEAM_SHOTS_OUTSIDEBOX_season_sum  HOME_TEAM_PASSES_season_sum  \
ID                                                                       
0                                     1.0                          2.0   
1                                     5.0                          8.0   
2                                     8.0                          1.0   
3                                     6.0                          9.0   
4                                     4.0                          4.0   

    HOME_TEAM_SUCCESSFUL_PASSES_season_sum  HOME_TEAM_SAVES_season_sum  \
ID                                                                       
0                                      2.0                         5.0   
1                                      7.0                        10.0   
2                                      1.0                         2.0   
3                                      9.0                         2.0   
4                                      3.0                         4.0   

    HOME_TEAM_CORNERS_season_sum  HOME_TEAM_FOULS_season_sum  \
ID                                                             
0                            3.0                         6.0   
1                            6.0                         8.0   
2                            2.0                         7.0   
3                            2.0                         0.0   
4                            4.0                         7.0   

    HOME_TEAM_YELLOWCARDS_season_sum  HOME_TEAM_REDCARDS_season_sum  \
ID                                                                    
0                                2.0                            2.0   
1                                3.0                            0.0   
2                                7.0                            6.0   
3                                0.0                            6.0   
4                                4.0                            6.0   

    HOME_TEAM_OFFSIDES_season_sum  HOME_TEAM_ATTACKS_season_sum  \
ID                                                                
0                             1.0                           2.0   
1                             7.0                           7.0   
2                             3.0                           4.0   
3                             8.0                           6.0   
4                             2.0                           4.0   

    HOME_TEAM_PENALTIES_season_sum  HOME_TEAM_SUBSTITUTIONS_season_sum  \
ID                                                                       
0                              6.0                                 8.0   
1                              6.0                                10.0   
2                              5.0                                10.0   
3      

In [39]:
# Exportation du fichier final

train_data.to_csv('../data/Train_Data/5_train_data.csv')